In [48]:
# Import Required Libraries
import numpy as np
import matplotlib.pyplot as plt
import requests

# To unzip the edf_dataset
import zipfile
import os

# EDFlib and Data Preprocesing module
from mne.preprocessing import ICA, create_eog_epochs
import mne
from pyedflib import highlevel
import pyedflib as plib


In [49]:
import requests


def download_file(url, save_path):

    # Check if the file already exists
    if os.path.exists(save_path):
        print(f"File already exists at '{save_path}'. Skipping download.")
        return  # Exit the function if the file exists

    # Send a GET request to the URL
    response = requests.get(url)

    # Check if the request was successful
    if response.status_code == 200:
        # Open the file in binary write mode and save the content
        with open(save_path, 'wb') as file:
            file.write(response.content)
        print(f"File downloaded successfully and saved to '{save_path}'")
    else:
        print(f"Failed to download file. Status code: {response.status_code}")


# Specify the URL and the path where you want to save the file
url = 'https://figshare.com/ndownloader/articles/4244171/versions/2'
# Change this to your desired path
save_path = './edf_dataset.zip'

# Call the function to download the file
download_file(url, save_path)

File already exists at './edf_dataset.zip'. Skipping download.


In [50]:
def unzip_file(zip_file_path, extract_to_folder):

    # Check if the directory exist

    if os.path.exists(extract_to_folder):
        print(f"Directory '{extract_to_folder} already exists")
        return  # Exit the function if the directory

    # Create the directory if it doesn't exist
    os.makedirs(extract_to_folder, exist_ok=True)

    # Open the zip file
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        # Extract all the contents into the specified folder
        zip_ref.extractall(extract_to_folder)


# Specify the path to the zip file and the extraction folder
zip_file_path = './edf_dataset.zip'
# Change this if needed
extract_to_folder = './edf_dataset_2'

# Call the function to unzip
unzip_file(zip_file_path, extract_to_folder)

Directory './edf_dataset_2 already exists


In [51]:
import os
import re  # Import the regular expressions module

# edf_directory
edf_directory = "./edf_dataset_2"
# Loop through all files in the specified directory
for filename in os.listdir(edf_directory):
    # Check if the filename contains spaces
    if ' ' in filename:
        # Create a new filename by replacing multiple spaces with a single underscore
        # Replace one or more spaces with a single underscore
        new_filename = re.sub(r'\s+', '_', filename)

        # Get the full path for the old and new filenames
        old_file = os.path.join(edf_directory, filename)
        new_file = os.path.join(edf_directory, new_filename)

        # Rename the file
        os.rename(old_file, new_file)
        print(f'Renamed: "{filename}" to "{new_filename}"')
    elif '6931959' in filename:
        new_filename = filename.replace('6921959_', '')

        # Get the full path for the old and new filenames
        old_file = os.path.join(edf_directory, filename)
        new_file = os.path.join(edf_directory, new_filename)

        # Rename the file
        os.rename(old_file, new_file)
        print(f'Renamed: "{filename}" to "{new_filename}"')
    elif '6921143' in filename:
        new_filename = filename.replace('6921143_', '')
        # Get the full path for the old and new filenames
        old_file = os.path.join(edf_directory, filename)
        new_file = os.path.join(edf_directory, new_filename)

        # Rename the file
        os.rename(old_file, new_file)
        print(f'Renamed: "{filename}" to "{new_filename}"')
print("Renaming complete.")

Renaming complete.


In [71]:
# Function to rename channels and drop specified channels based on conditions
def process_channels(raw_data):
    """
    Process and standardize EEG channels to keep only the 17 most common channels.
    """
    print(f"Initial channels: {raw_data.ch_names}")

    # Initialize a list to hold channels to drop
    channels_to_drop = []

    # Create mapping for channel renaming
    rename_map = {}
    for name in raw_data.ch_names:
        if any(x in name for x in ['23A-23R', '24A-24R', 'A2-A1']):
            channels_to_drop.append(name)
        else:
            new_name = name.replace('EEG ', '').replace('-LE', '')
            rename_map[name] = new_name

    # Drop unwanted channels
    if channels_to_drop:
        print(f"Dropping channels: {channels_to_drop}")
        raw_data.drop_channels(channels_to_drop)

    # Rename remaining channels
    raw_data.rename_channels(rename_map)

    print(f"Final channels: {raw_data.ch_names}")

    # Define the 17 most common channels
    expected_channels = [
        'Fp1', 'F3', 'C3', 'P3', 'O1', 'F7', 'T3', 'Fp2',
        'F4', 'C4', 'P4', 'O2', 'F8', 'T4', 'T6', 'Cz', 'Pz'
    ]

    # Keep only the expected channels
    channels_to_keep = set(expected_channels)
    channels_to_drop = [
        ch for ch in raw_data.ch_names if ch not in channels_to_keep]

    if channels_to_drop:
        print(
            f"Dropping channels to keep only the expected 17 channels: {channels_to_drop}")
        raw_data.drop_channels(channels_to_drop)

    # Verify we have the expected number of channels (should be 17)
    if len(raw_data.ch_names) != len(expected_channels):
        print(
            f"Warning: Expected {len(expected_channels)} channels, got {len(raw_data.ch_names)}")
        print(f"Missing: {set(expected_channels) - set(raw_data.ch_names)}")

    return raw_data

In [53]:
all_edf_files = os.listdir(edf_directory)
ec_file_path = [i for i in all_edf_files if i.endswith('EC.edf')]
eo_file_path = [i for i in all_edf_files if i.endswith('EO.edf')]
task_file_path = [i for i in all_edf_files if i.endswith('TASK.edf')]

print(len(all_edf_files), len(ec_file_path),
      len(eo_file_path), len(task_file_path))

180 58 61 61


In [54]:
def read_data(file_path):
    data = mne.io.read_raw_edf(file_path, preload=True)
    data.set_eeg_reference()
    return data

In [55]:
def bandpass_filter(data, l_freq, h_freq, notch_freq=None):
    filtered_data = data.copy()

    # Apply bandpass first
    filtered_data.filter(l_freq=l_freq, h_freq=h_freq,
                         method='fir', phase='zero')

    # If using notch, apply with wider bandwidth
    if notch_freq is not None:
        filtered_data.notch_filter(freqs=notch_freq, notch_widths=2.0)

    return filtered_data

In [56]:
all_edf_files = os.listdir(edf_directory)
ec_file_path = [i for i in all_edf_files if i.endswith('EC.edf')]
eo_file_path = [i for i in all_edf_files if i.endswith('EO.edf')]
task_file_path = [i for i in all_edf_files if i.endswith('TASK.edf')]

print(len(all_edf_files), len(ec_file_path),
      len(eo_file_path), len(task_file_path))

180 58 61 61


In [57]:
ica_channels = ['Fp1', 'Fp2']

In [58]:
def preprocess_ICA(epochs, n_components):
    """
    Apply Independent Component Analysis (ICA) to the epochs data.
    
    Parameters:
    -----------
    epochs : mne.Epochs
        The epochs data to process.
    n_components : int
        The number of components to extract.
    
    Returns:
    --------
    ica : ICA
        The fitted ICA object.
    """
    print(
        f"Preprocessing ICA for {len(epochs)} epochs...")  # Print the number of epochs being processed

    ica = ICA(n_components=n_components, random_state=97, max_iter=800)
    # Use the epochs directly
    ica.fit(epochs.copy().pick_channels(ica_channels))
    return ica

In [59]:
def create_epochs(processed_data, duration=5.0, overlap=1.0):
    """
    Create epochs from continuous EEG data and format for CNN input
    
    Parameters:
    -----------
    processed_data : mne.io.Raw
        The raw EEG data
    duration : float
        Duration of each epoch in seconds
    overlap : float
        Overlap between epochs in seconds
    
    Returns:
    --------
    epochs_array : numpy.ndarray
        The epoched data formatted for CNN (samples, channels, timepoints, 1)
    """

    # Create epochs
    epochs = mne.make_fixed_length_epochs(
        processed_data,
        duration=duration,
        overlap=overlap,
        preload=True
    )

    # Drop bad epochs
    epochs.drop_bad()

    # Get data and reshape for CNN
    # Shape will be (n_epochs, n_channels, n_timepoints)
    data = epochs.get_data()

    # Add channel dimension for CNN: (n_epochs, n_channels, n_timepoints, 1)
    data = data[..., np.newaxis]

    return data

In [60]:
# Directory containing the EDF files
edf_directory = "./edf_dataset_2"  # Adjust this path to your dataset location

# Initialize lists
processed_raw_data = []
class_counts = {'Healthy': 0, 'MDD': 0}

# Read all EDF files
for filename in os.listdir(edf_directory):
    if filename.endswith('.edf'):
        file_path = os.path.join(edf_directory, filename)
        try:
            # Read the raw data
            raw_data = read_data(file_path)

            if raw_data is not None:
                processed_raw_data.append(raw_data)
                print(f"Successfully loaded: {filename}")
            else:
                print(f"Failed to load: {filename}")

        except Exception as e:
            print(f"Error loading {filename}: {str(e)}")
            continue

print(f"\nTotal files loaded: {len(processed_raw_data)}")

Extracting EDF parameters from /Users/hansandreanto/Development/capstone-project/edf_dataset_2/H_S4_TASK.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 154879  =      0.000 ...   604.996 secs...
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
Successfully loaded: H_S4_TASK.edf
Extracting EDF parameters from /Users/hansandreanto/Development/capstone-project/edf_dataset_2/H_S5_TASK.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 156671  =      0.000 ...   611.996 secs...
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
Successfully loaded: H_S5_TASK.edf
Extracting EDF parameters from /Users/hansandreanto/Development/capstone-project/edf_dataset_2/H_S16_EO.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 

In [72]:
def preprocess_eeg(raw_data, task_type, l_freq=0.5, h_freq=60.0, notch_freq=50.0, n_components=2, epoch_duration=5.0, epoch_overlap=1.0):
    """
    Complete EEG preprocessing pipeline with task type encoding
    """
    try:
        processed_raw = raw_data.copy()

        # 1. Bandpass filtering
        print("1. Applying bandpass filter...")
        try:
            bandpass_filter(processed_raw, l_freq, h_freq, notch_freq)
            print("Bandpass filtering completed")
        except Exception as e:
            print(f"Error during bandpass filtering: {str(e)}")
            return None, None

        # 2. Bad channel removal
        print("2. Removing bad channels...")
        try:
            processed_raw = process_channels(raw_data=processed_raw)
            print("Bad channels removed")
        except Exception as e:
            print(f"Error during bad channel removal: {str(e)}")
            return None, None

        # 3. Epoching
        print("3. Creating epochs...")
        try:
            epochs = mne.make_fixed_length_epochs(
                processed_raw,
                duration=epoch_duration,
                overlap=epoch_overlap,
                preload=True
            )
            epochs.drop_bad()
        except Exception as e:
            print(f"Error during epoching: {str(e)}")
            return None, None

        # 4. ICA
        print("4. Applying ICA...")
        try:
            ica = preprocess_ICA(epochs, n_components)
            ica.apply(epochs)
            print("ICA completed")
        except Exception as e:
            print(f"Error during ICA: {str(e)}")
            return None, None

        # 5. Baseline correction
        print("5. Applying baseline correction...")
        try:
            epochs.apply_baseline((None, None))
            print("Baseline correction completed")
        except Exception as e:
            print(f"Error during baseline correction: {str(e)}")
            return None, None

        # 6. Reshape for CNN-LSTM and prepare task encoding
        print("6. Reshaping data and encoding task...")
        try:
            data = epochs.get_data()
            n_epochs, n_channels, n_times = data.shape
            time_steps = 5
            window_size = n_times // time_steps

            reshaped_data = np.zeros(
                (n_epochs, time_steps, n_channels, window_size))
            for epoch_idx in range(n_epochs):
                for step in range(time_steps):
                    start_idx = step * window_size
                    end_idx = start_idx + window_size
                    reshaped_data[epoch_idx, step, :,
                                  :] = data[epoch_idx, :, start_idx:end_idx]

            final_data = reshaped_data[..., np.newaxis]

            # Create task encoding
            task_encoding = {
                'EC': [1, 0, 0],
                'EO': [0, 1, 0],
                'TASK': [0, 0, 1]
            }

            print(f"Reshaping completed. Final data shape: {final_data.shape}")
            return final_data, task_encoding[task_type]

        except Exception as e:
            print(f"Error during reshaping: {str(e)}")
            return None, None

    except Exception as e:
        print(f"General preprocessing error: {str(e)}")
        return None, None

In [73]:
# Data collection
X_eeg = []
X_task = []
y_labels = []

In [74]:

print("\nStarting preprocessing pipeline...")

for raw_data in processed_raw_data:
    # Get the filename from the raw data
    filename = os.path.basename(raw_data.filenames[0])
    print(f"\n{'='*50}")
    print(f"Processing: {filename}")
    print(f"Initial data info:")
    print(f"Channels: {raw_data.ch_names}")
    print(f"Sample rate: {raw_data.info['sfreq']} Hz")
    print(f"Duration: {raw_data.n_times / raw_data.info['sfreq']:.2f} seconds")

    # Determine task type
    if 'EC.edf' in filename:
        task_type = 'EC'
    elif 'EO.edf' in filename:
        task_type = 'EO'
    else:
        task_type = 'TASK'

    # Process data
    processed_data, task_info = preprocess_eeg(raw_data, task_type)

    if processed_data is not None:
        X_eeg.append(processed_data)
        X_task.extend([task_info] * processed_data.shape[0])
        label = 1 if filename.startswith('MDD') else 0
        y_labels.extend([label] * processed_data.shape[0])
        print(f"Shape of the X_EEG: {X_eeg}")


Starting preprocessing pipeline...

Processing: H_S4_TASK.edf
Initial data info:
Channels: ['EEG Fp1-LE', 'EEG F3-LE', 'EEG C3-LE', 'EEG P3-LE', 'EEG O1-LE', 'EEG F7-LE', 'EEG T3-LE', 'EEG T5-LE', 'EEG Fz-LE', 'EEG Fp2-LE', 'EEG F4-LE', 'EEG C4-LE', 'EEG P4-LE', 'EEG O2-LE', 'EEG F8-LE', 'EEG T4-LE', 'EEG T6-LE', 'EEG Cz-LE', 'EEG Pz-LE', 'EEG A2-A1', 'EEG 23A-23R', 'EEG 24A-24R']
Sample rate: 256.0 Hz
Duration: 605.00 seconds
1. Applying bandpass filter...
Filtering raw data in 1 contiguous segment
Setting up band-pass filter from 0.5 - 60 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.50
- Lower transition bandwidth: 0.50 Hz (-6 dB cutoff frequency: 0.25 Hz)
- Upper passband edge: 60.00 Hz
- Upper transition bandwidth: 15.00 Hz (-6 dB cutoff frequency: 67.50 Hz)
- Filter lengt

Bandpass filtering completed
2. Removing bad channels...
Initial channels: ['EEG Fp1-LE', 'EEG F3-LE', 'EEG C3-LE', 'EEG P3-LE', 'EEG O1-LE', 'EEG F7-LE', 'EEG T3-LE', 'EEG T5-LE', 'EEG Fz-LE', 'EEG Fp2-LE', 'EEG F4-LE', 'EEG C4-LE', 'EEG P4-LE', 'EEG O2-LE', 'EEG F8-LE', 'EEG T4-LE', 'EEG T6-LE', 'EEG Cz-LE', 'EEG Pz-LE', 'EEG A2-A1', 'EEG 23A-23R', 'EEG 24A-24R']
Dropping channels: ['EEG A2-A1', 'EEG 23A-23R', 'EEG 24A-24R']
Final channels: ['Fp1', 'F3', 'C3', 'P3', 'O1', 'F7', 'T3', 'T5', 'Fz', 'Fp2', 'F4', 'C4', 'P4', 'O2', 'F8', 'T4', 'T6', 'Cz', 'Pz']
Dropping channels to keep only the expected 17 channels: ['T5', 'Fz']
Bad channels removed
3. Creating epochs...
Not setting metadata
151 matching events found
No baseline correction applied
0 projection items activated
Using data from preloaded Raw for 151 events and 1280 original time points ...
0 bad epochs dropped
4. Applying ICA...
Preprocessing ICA for 151 epochs...


/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1724: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and wi

Fitting ICA to data using 2 channels (please be patient, this may take a while)
Selecting by number: 2 components
Fitting ICA took 0.3s.
Applying ICA to Epochs instance
    Transforming to ICA space (2 components)
    Zeroing out 0 ICA components
    Projecting back using 2 PCA components
ICA completed
5. Applying baseline correction...
Applying baseline correction (mode: mean)
Baseline correction completed
6. Reshaping data and encoding task...
Reshaping completed. Final data shape: (151, 5, 17, 256, 1)
Shape of the X_EEG: [array([[[[[-7.19218221e-06],
          [-4.87836933e-06],
          [-2.90549154e-06],
          ...,
          [-2.75119142e-05],
          [-2.60390746e-05],
          [-2.62299982e-05]],

         [[ 1.24029064e-05],
          [ 9.31630733e-06],
          [ 6.98885704e-06],
          ...,
          [ 2.88399843e-06],
          [ 3.56532881e-07],
          [-4.23472647e-06]],

         [[-8.01538422e-07],
          [-4.08815279e-06],
          [-2.71532079e-06],


/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1724: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and wi

...

Selecting by number: 2 components
Fitting ICA took 0.3s.
Applying ICA to Epochs instance
    Transforming to ICA space (2 components)
    Zeroing out 0 ICA components
    Projecting back using 2 PCA components
ICA completed
5. Applying baseline correction...
Applying baseline correction (mode: mean)
Baseline correction completed
6. Reshaping data and encoding task...
Reshaping completed. Final data shape: (74, 5, 17, 256, 1)
Shape of the X_EEG: [array([[[[[-7.19218221e-06],
          [-4.87836933e-06],
          [-2.90549154e-06],
          ...,
          [-2.75119142e-05],
          [-2.60390746e-05],
          [-2.62299982e-05]],

         [[ 1.24029064e-05],
          [ 9.31630733e-06],
          [ 6.98885704e-06],
          ...,
          [ 2.88399843e-06],
          [ 3.56532881e-07],
          [-4.23472647e-06]],

         [[-8.01538422e-07],
          [-4.08815279e-06],
          [-2.71532079e-06],
          ...,
          [-9.82040828e-06],
          [-7.34749235e-06],
        

/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1724: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and wi

Bandpass filtering completed
2. Removing bad channels...
Initial channels: ['EEG Fp1-LE', 'EEG F3-LE', 'EEG C3-LE', 'EEG P3-LE', 'EEG O1-LE', 'EEG F7-LE', 'EEG T3-LE', 'EEG T5-LE', 'EEG Fz-LE', 'EEG Fp2-LE', 'EEG F4-LE', 'EEG C4-LE', 'EEG P4-LE', 'EEG O2-LE', 'EEG F8-LE', 'EEG T4-LE', 'EEG T6-LE', 'EEG Cz-LE', 'EEG Pz-LE', 'EEG A2-A1']
Dropping channels: ['EEG A2-A1']
Final channels: ['Fp1', 'F3', 'C3', 'P3', 'O1', 'F7', 'T3', 'T5', 'Fz', 'Fp2', 'F4', 'C4', 'P4', 'O2', 'F8', 'T4', 'T6', 'Cz', 'Pz']
Dropping channels to keep only the expected 17 channels: ['T5', 'Fz']
Bad channels removed
3. Creating epochs...
Not setting metadata
75 matching events found
No baseline correction applied
0 projection items activated
Using data from preloaded Raw for 75 events and 1280 original time points ...
0 bad epochs dropped
4. Applying ICA...
Preprocessing ICA for 75 epochs...
Fitting ICA to data using 2 channels (please be patient, this may take a while)
Selecting by number: 2 components
Fitting IC

/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1008: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  logger.info('Setting up band-pass filter from %0.2g - %0.2g Hz'
/Users/hansandreanto/Development/capstone-project/capstone_env/lib/python3.11/site-packages/mne/filter.py:1724: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and wi

Selecting by number: 2 components
Fitting ICA took 0.2s.
Applying ICA to Epochs instance
    Transforming to ICA space (2 components)
    Zeroing out 0 ICA components
    Projecting back using 2 PCA components
ICA completed
5. Applying baseline correction...
Applying baseline correction (mode: mean)


In [67]:
# Convert lists to arrays
X_eeg = np.concatenate(X_eeg, axis=0)
X_task = np.array(X_task)
y_labels = np.array(y_labels)

# Check shapes
print("X_eeg shape:", X_eeg.shape)  
print("X_task shape:", X_task.shape)  
print("y_labels shape:", y_labels.shape)  

ValueError: need at least one array to concatenate

In [37]:
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, Dense, LSTM, Dropout, Flatten, Reshape, TimeDistributed


def create_2dcnn_lstm_model(input_shape=(5, 17, 256, 1), task_shape=(3,)):
    # EEG input branch
    eeg_input = Input(shape=input_shape, name='eeg_input')

    # Task input branch
    task_input = Input(shape=task_shape, name='task_input')

    # CNN-LSTM branch for EEG
    x = TimeDistributed(
        Conv2D(64, (3, 3), activation='relu', padding='same'))(eeg_input)
    x = TimeDistributed(MaxPooling2D((2, 2)))(x)

    x = TimeDistributed(
        Conv2D(128, (3, 3), activation='relu', padding='same'))(x)
    x = TimeDistributed(MaxPooling2D((2, 2)))(x)

    x = TimeDistributed(
        Conv2D(256, (3, 3), activation='relu', padding='same'))(x)
    x = TimeDistributed(MaxPooling2D((2, 2)))(x)

    x = TimeDistributed(Flatten())(x)

    x = LSTM(128, return_sequences=True)(x)
    x = LSTM(64)(x)

    # Process task input
    task_features = Dense(32, activation='relu')(task_input)

    # Concatenate EEG features with task features
    combined = tf.keras.layers.Concatenate()([x, task_features])

    # Dense layers after combining
    x = Dense(128, activation='relu')(combined)
    x = Dropout(0.5)(x)
    x = Dense(64, activation='relu')(x)
    x = Dropout(0.5)(x)

    # Output layer
    outputs = Dense(1, activation='sigmoid')(x)

    model = Model(inputs=[eeg_input, task_input], outputs=outputs)
    return model

In [ ]:
from sklearn.model_selection import train_test_split


def prepare_data(X_eeg, X_task, y_labels):
    # Normalize the EEG data
    X_eeg = (X_eeg - X_eeg.mean()) / X_eeg.std()

    # Train-test split
    X_eeg_train, X_eeg_test, X_task_train, X_task_test, y_train, y_test = train_test_split(
        X_eeg, X_task, y_labels, test_size=0.2, random_state=42, stratify=y_labels
    )

    return X_eeg_train, X_eeg_test, X_task_train, X_task_test, y_train, y_test

In [ ]:
def train_model(model, X_eeg_train, X_task_train, y_train, X_eeg_test, X_task_test, y_test):
    # Compile model
    model.compile(
        optimizer='adam',
        loss='binary_crossentropy',
        metrics=['accuracy', tf.keras.metrics.AUC()]
    )

    # Callbacks
    callbacks = [
        tf.keras.callbacks.EarlyStopping(
            monitor='val_loss', patience=5, restore_best_weights=True
        ),
        tf.keras.callbacks.ReduceLROnPlateau(
            monitor='val_loss', factor=0.5, patience=5, min_lr=1e-6
        )
    ]

    # Train model
    history = model.fit(
        [X_eeg_train, X_task_train], y_train,
        validation_data=([X_eeg_test, X_task_test], y_test),
        epochs=25,
        batch_size=32,
        callbacks=callbacks
    )

    return history

In [ ]:
import seaborn as sns
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix
import matplotlib.pyplot as plt


def evaluate_model(model, X_eeg_train, X_task_train, y_train, X_eeg_test, X_task_test, y_test):
    # Training predictions
    y_train_pred = model.predict([X_eeg_train, X_task_train])
    y_train_pred_classes = (y_train_pred > 0.5).astype(int)

    # Test predictions
    y_test_pred = model.predict([X_eeg_test, X_task_test])
    y_test_pred_classes = (y_test_pred > 0.5).astype(int)

    # Calculate training metrics
    train_accuracy = accuracy_score(y_train, y_train_pred_classes)
    train_precision = precision_score(y_train, y_train_pred_classes)
    train_recall = recall_score(y_train, y_train_pred_classes)
    train_f1 = f1_score(y_train, y_train_pred_classes)
    train_auc = roc_auc_score(y_train, y_train_pred)

    # Calculate test metrics
    test_accuracy = accuracy_score(y_test, y_test_pred_classes)
    test_precision = precision_score(y_test, y_test_pred_classes)
    test_recall = recall_score(y_test, y_test_pred_classes)
    test_f1 = f1_score(y_test, y_test_pred_classes)
    test_auc = roc_auc_score(y_test, y_test_pred)

    # Print results
    print("\nTraining Results:")
    print(f"Accuracy: {train_accuracy:.4f}")
    print(f"Precision: {train_precision:.4f}")
    print(f"Recall: {train_recall:.4f}")
    print(f"F1-Score: {train_f1:.4f}")
    print(f"AUC-ROC: {train_auc:.4f}")

    print("\nTest Results:")
    print(f"Accuracy: {test_accuracy:.4f}")
    print(f"Precision: {test_precision:.4f}")
    print(f"Recall: {test_recall:.4f}")
    print(f"F1-Score: {test_f1:.4f}")
    print(f"AUC-ROC: {test_auc:.4f}")

    # Plot confusion matrices
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(16, 6))

    # Training confusion matrix
    cm_train = confusion_matrix(y_train, y_train_pred_classes)
    sns.heatmap(cm_train, annot=True, fmt='d', cmap='Greens', ax=ax1)
    ax1.set_title('Training Confusion Matrix')
    ax1.set_ylabel('True Label')
    ax1.set_xlabel('Predicted Label')

    # Testing confusion matrix
    cm_test = confusion_matrix(y_test, y_test_pred_classes)
    sns.heatmap(cm_test, annot=True, fmt='d', cmap='Blues', ax=ax2)
    ax2.set_title('Testing Confusion Matrix')
    ax2.set_ylabel('True Label')
    ax2.set_xlabel('Predicted Label')

    plt.tight_layout()
    plt.show()

In [ ]:
# Prepare data
X_eeg_train, X_eeg_test, X_task_train, X_task_test, y_train, y_test = prepare_data(
    X_eeg, X_task, y_labels)

# Create and train model
input_shape = (5, 17, 256, 1)
task_shape = (3,)
model = create_2dcnn_lstm_model(input_shape, task_shape)
history = train_model(model, X_eeg_train, X_task_train,
                      y_train, X_eeg_test, X_task_test, y_test)

In [ ]:
# Evaluate model
evaluate_model(model, X_eeg_train, X_task_train,
               y_train, X_eeg_test, X_task_test, y_test)

In [ ]:
def plot_training_history(history, y_test, X_test, model):
    # Get predictions for ROC curve
    y_pred = model.predict(X_test)

    # Create figure with subplots
    fig, axes = plt.subplots(1, 3, figsize=(18, 6))

    # Plot 1: ROC Curve
    fpr, tpr, _ = roc_curve(y_test, y_pred)
    roc_auc = auc(fpr, tpr)

    axes[0].plot(fpr, tpr, 'b-', label=f'ROC (AUC = {roc_auc:.3f})')
    axes[0].plot([0, 1], [0, 1], 'r--')
    axes[0].set_xlabel('False Positive Rate')
    axes[0].set_ylabel('True Positive Rate')
    axes[0].set_title('ROC Curve')
    axes[0].legend(loc='lower right')
    axes[0].grid(True)

    # Plot 2: Accuracy
    axes[1].plot(history.history['accuracy'], 'b-', label='Training')
    axes[1].plot(history.history['val_accuracy'], 'r-', label='Validation')
    axes[1].set_xlabel('Epoch')
    axes[1].set_ylabel('Accuracy')
    axes[1].set_title('Model Accuracy')
    axes[1].legend(loc='lower right')
    axes[1].grid(True)

    # Plot 3: Loss
    axes[2].plot(history.history['loss'], 'b-', label='Training')
    axes[2].plot(history.history['val_loss'], 'r-', label='Validation')
    axes[2].set_xlabel('Epoch')
    axes[2].set_ylabel('Loss')
    axes[2].set_title('Model Loss')
    axes[2].legend(loc='upper right')
    axes[2].grid(True)

    plt.tight_layout()
    plt.show()


# Usage after training
plot_training_history(history, y_test, X_test, model)

# # You can also access individual metrics from history
# print("\nTraining History Summary:")
# print(f"Final training accuracy: {history.history['accuracy'][-1]:.4f}")
# print(f"Final validation accuracy: {history.history['val_accuracy'][-1]:.4f}")
# print(f"Final training loss: {history.history['loss'][-1]:.4f}")
# print(f"Final validation loss: {history.history['val_loss'][-1]:.4f}")

# # Plot learning curves separately if needed
# plt.figure(figsize=(12, 4))
# plt.subplot(1, 2, 1)
# plt.plot(history.history['accuracy'])
# plt.plot(history.history['val_accuracy'])
# plt.title('Model Accuracy Over Time')
# plt.ylabel('Accuracy')
# plt.xlabel('Epoch')
# plt.legend(['Train', 'Validation'], loc='lower right')

# plt.subplot(1, 2, 2)
# plt.plot(history.history['loss'])
# plt.plot(history.history['val_loss'])
# plt.title('Model Loss Over Time')
# plt.ylabel('Loss')
# plt.xlabel('Epoch')
# plt.legend(['Train', 'Validation'], loc='upper right')
# plt.tight_layout()
# plt.show()